## BICYCLE THEFT IN TORONTO 2019

# A. Introduction

The objective of this project is to determine the clusters with the highest bicycle theft in Toronto in 2019. This project can become an important input for the Toronto Police Department to implement measures to ensure the safety of city dwellers.

# B. Data Description

I will use the dataset that contains Bicycle Thefts occurrences from 2014-2019 of the Toronto Police Service Public Safety Data Portal. I will filter only the information of the year 2019.

# C. Methodology

In [231]:
import pandas as pd
import numpy as np
import requests # library to handle requests
from sklearn.cluster import KMeans
import matplotlib.cm as cm
import matplotlib.colors as colors
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
!pip install folium==0.5.0
import folium # map rendering library
print('Libraries imported.')

Libraries imported.


In [232]:
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize

In [233]:
CLIENT_ID = 'JRBHXSAPVLFOMM3HB1JTGFOR4KPPWXALLREDW4ZY0RBFNB25' # your Foursquare ID
CLIENT_SECRET = 'GJSLRP4TE2DLT300PQLVZTQXBH41PFYGMRORADYWUEEJEO5P' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: JRBHXSAPVLFOMM3HB1JTGFOR4KPPWXALLREDW4ZY0RBFNB25
CLIENT_SECRET:GJSLRP4TE2DLT300PQLVZTQXBH41PFYGMRORADYWUEEJEO5P


In [234]:

import types
import pandas as pd
from botocore.client import Config
import ibm_boto3

def __iter__(self): return 0

# @hidden_cell
# The following code accesses a file in your IBM Cloud Object Storage. It includes your credentials.
# You might want to remove those credentials before you share the notebook.
client_760475e9882e4f29a4cbb23964c7161a = ibm_boto3.client(service_name='s3',
    ibm_api_key_id='5WhqIPVm_y3ny8aNy0e9ebDizz19hO5DAhm5ooiIfsxV',
    ibm_auth_endpoint="https://iam.cloud.ibm.com/oidc/token",
    config=Config(signature_version='oauth'),
    endpoint_url='https://s3-api.us-geo.objectstorage.service.networklayer.com')

body = client_760475e9882e4f29a4cbb23964c7161a.get_object(Bucket='finalprojectcapstone-donotdelete-pr-fnidpwaatvxtul',Key='Bycicle_Thets.xlsx')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_data_0 = pd.read_excel(body)
df_data_0.head()


X             Y  FID  Index_ event_unique_id   Primary_Offence  \
0 -8.858872e+06  5.425243e+06    1     201  GO-20142058713       THEFT UNDER   
1 -8.834825e+06  5.419675e+06    2     202  GO-20142059340  PROPERTY - FOUND   
2 -8.836985e+06  5.413433e+06    3     203  GO-20142060810       THEFT UNDER   
3 -8.826689e+06  5.417104e+06    4     204  GO-20142062543       THEFT UNDER   
4 -8.826689e+06  5.417104e+06    5     205  GO-20142062543       THEFT UNDER   

  Occurrence_Date  Occurrence_Year  Occurrence_Month  Occurrence_Day  ...  \
0      2014-05-10             2014                 5              10  ...   
1      2014-05-11             2014                 5              11  ...   
2      2014-05-11             2014                 5              11  ...   
3      2014-05-11             2014                 5              11  ...   
4      2014-05-11             2014                 5              11  ...   

        Bike_Model  Bike_Type Bike_Speed Bike_Colour Cost_of_Bike     Status  \
0              NaN         MT         10      ONG             NaN     STOLEN   
1  TRAILHEAD               MT          1      BLK             NaN  RECOVERED   
2              NaN         MT         18      BLU           200.0     STOLEN   
3              NaN         OT         24      WHI          1600.0     STOLEN   
4              NaN         OT         18      BLU           650.0     STOLEN   

  Hood_ID                          Neighbourhood        Lat       Long  
0       2  Mount Olive-Silverstone-Jamestown (2)  43.739670 -79.580597  
1      56                Leaside-Bennington (56)  43.703518 -79.364586  
2      76               Bay Street Corridor (76)  43.662968 -79.383987  
3      62                 East End-Danforth (62)  43.686817 -79.291496  
4      62                 East End-Danforth (62)  43.686817 -79.291496  

[5 rows x 26 columns]

In [174]:
df_data_0.shape

(21584, 26)

In [175]:
df_data_0.columns

Index(['X', 'Y', 'FID', 'Index_', 'event_unique_id', 'Primary_Offence',
       'Occurrence_Date', 'Occurrence_Year', 'Occurrence_Month',
       'Occurrence_Day', 'Occurrence_Time', 'Division', 'City',
       'Location_Type', 'Premise_Type', 'Bike_Make', 'Bike_Model', 'Bike_Type',
       'Bike_Speed', 'Bike_Colour', 'Cost_of_Bike', 'Status', 'Hood_ID',
       'Neighbourhood', 'Lat', 'Long'],
      dtype='object')

In [176]:
df_data_0.dtypes

X                          float64
Y                          float64
FID                          int64
Index_                       int64
event_unique_id             object
Primary_Offence             object
Occurrence_Date     datetime64[ns]
Occurrence_Year              int64
Occurrence_Month             int64
Occurrence_Day               int64
Occurrence_Time             object
Division                     int64
City                        object
Location_Type               object
Premise_Type                object
Bike_Make                   object
Bike_Model                  object
Bike_Type                   object
Bike_Speed                   int64
Bike_Colour                 object
Cost_of_Bike               float64
Status                      object
Hood_ID                      int64
Neighbourhood               object
Lat                        float64
Long                       float64
dtype: object

In [177]:
df_data_0.describe()

X             Y           FID        Index_  \
count  2.158400e+04  2.158400e+04  21584.000000  21584.000000   
mean  -8.838312e+06  5.414897e+06  10792.500000  10931.509544   
std    6.681736e+03  5.833749e+03   6230.908441   6311.114639   
min   -8.863526e+06  5.401795e+06      1.000000      1.000000   
25%   -8.841113e+06  5.411416e+06   5396.750000   5465.750000   
50%   -8.837888e+06  5.413239e+06  10792.500000  10930.500000   
75%   -8.835999e+06  5.415879e+06  16188.250000  16401.250000   
max   -8.807967e+06  5.440182e+06  21584.000000  22061.000000   

       Occurrence_Year  Occurrence_Month  Occurrence_Day      Division  \
count     21584.000000      21584.000000    21584.000000  21584.000000   
mean       2016.623934          7.176149       15.621016     37.040400   
std           1.662515          2.508756        8.552982     17.644204   
min        2014.000000          1.000000        1.000000     11.000000   
25%        2015.000000          6.000000        8.000000     14.000000   
50%        2017.000000          7.000000       16.000000     51.000000   
75%        2018.000000          9.000000       23.000000     52.000000   
max        2019.000000         12.000000       31.000000     58.000000   

         Bike_Speed   Cost_of_Bike       Hood_ID           Lat          Long  
count  21584.000000   20048.000000  21584.000000  21584.000000  21584.000000  
mean      14.161462     937.977861     75.254679     43.672466    -79.395912  
std       10.556898    1730.177314     23.919558      0.037886      0.060023  
min        0.000000       0.000000      1.000000     43.587292    -79.622406  
25%        6.000000     350.000000     71.000000     43.649860    -79.421066  
50%       15.000000     600.000000     77.000000     43.661705    -79.392098  
75%       21.000000    1000.000000     85.000000     43.678860    -79.375130  
max       99.000000  120000.000000    140.000000     43.836544    -79.123314

In [178]:
df_data_0.describe(include = "all")

X             Y           FID        Index_  \
count   2.158400e+04  2.158400e+04  21584.000000  21584.000000   
unique           NaN           NaN           NaN           NaN   
top              NaN           NaN           NaN           NaN   
freq             NaN           NaN           NaN           NaN   
first            NaN           NaN           NaN           NaN   
last             NaN           NaN           NaN           NaN   
mean   -8.838312e+06  5.414897e+06  10792.500000  10931.509544   
std     6.681736e+03  5.833749e+03   6230.908441   6311.114639   
min    -8.863526e+06  5.401795e+06      1.000000      1.000000   
25%    -8.841113e+06  5.411416e+06   5396.750000   5465.750000   
50%    -8.837888e+06  5.413239e+06  10792.500000  10930.500000   
75%    -8.835999e+06  5.415879e+06  16188.250000  16401.250000   
max    -8.807967e+06  5.440182e+06  21584.000000  22061.000000   

       event_unique_id Primary_Offence      Occurrence_Date  Occurrence_Year  \
count            21584           21584                21584     21584.000000   
unique           19350              65                 2104              NaN   
top      GO-2017637379     THEFT UNDER  2018-08-15 00:00:00              NaN   
freq                14            9784                   39              NaN   
first              NaN             NaN  2014-01-01 00:00:00              NaN   
last               NaN             NaN  2019-12-31 00:00:00              NaN   
mean               NaN             NaN                  NaN      2016.623934   
std                NaN             NaN                  NaN         1.662515   
min                NaN             NaN                  NaN      2014.000000   
25%                NaN             NaN                  NaN      2015.000000   
50%                NaN             NaN                  NaN      2017.000000   
75%                NaN             NaN                  NaN      2018.000000   
max                NaN             NaN                  NaN      2019.000000   

        Occurrence_Month  Occurrence_Day  ...       Bike_Model  Bike_Type  \
count       21584.000000    21584.000000  ...            13443      21584   
unique               NaN             NaN  ...             7008         13   
top                  NaN             NaN  ...  UNKNOWN                 MT   
freq                 NaN             NaN  ...              265       6915   
first                NaN             NaN  ...              NaN        NaN   
last                 NaN             NaN  ...              NaN        NaN   
mean            7.176149       15.621016  ...              NaN        NaN   
std             2.508756        8.552982  ...              NaN        NaN   
min             1.000000        1.000000  ...              NaN        NaN   
25%             6.000000        8.000000  ...              NaN        NaN   
50%             7.000000       16.000000  ...              NaN        NaN   
75%             9.000000       23.000000  ...              NaN        NaN   
max            12.000000       31.000000  ...              NaN        NaN   

          Bike_Speed Bike_Colour   Cost_of_Bike  Status       Hood_ID  \
count   21584.000000       19855   20048.000000   21584  21584.000000   
unique           NaN         233            NaN       3           NaN   
top              NaN      BLK               NaN  STOLEN           NaN   
freq             NaN        6212            NaN   20929           NaN   
first            NaN         NaN            NaN     NaN           NaN   
last             NaN         NaN            NaN     NaN           NaN   
mean       14.161462         NaN     937.977861     NaN     75.254679   
std        10.556898         NaN    1730.177314     NaN     23.919558   
min         0.000000         NaN       0.000000     NaN      1.000000   
25%         6.000000         NaN     350.000000     NaN     71.000000   
50%        15.000000         NaN     600.000000     NaN     77.000000   
75%        21.0000

In [179]:
df_data_0.info

<bound method DataFrame.info of                   X             Y    FID  Index_ event_unique_id  \
0     -8.858872e+06  5.425243e+06      1     201  GO-20142058713   
1     -8.834825e+06  5.419675e+06      2     202  GO-20142059340   
2     -8.836985e+06  5.413433e+06      3     203  GO-20142060810   
3     -8.826689e+06  5.417104e+06      4     204  GO-20142062543   
4     -8.826689e+06  5.417104e+06      5     205  GO-20142062543   
5     -8.846058e+06  5.411974e+06      6     206  GO-20142063112   
6     -8.836715e+06  5.413999e+06      7     207  GO-20142064711   
7     -8.837621e+06  5.413773e+06      8     208  GO-20142065788   
8     -8.835320e+06  5.412506e+06      9     209  GO-20142065987   
9     -8.838608e+06  5.414173e+06     10     210  GO-20142066066   
10    -8.837219e+06  5.412504e+06     11     211  GO-20142066244   
11    -8.834929e+06  5.412085e+06     12     212  GO-20142068530   
12    -8.834929e+06  5.412085e+06     13     213  GO-20142068530   
13    -8.840278e

In [180]:
missing_data = df_data_0.isnull()
missing_data.head(5)

X      Y    FID  Index_  event_unique_id  Primary_Offence  \
0  False  False  False   False            False            False   
1  False  False  False   False            False            False   
2  False  False  False   False            False            False   
3  False  False  False   False            False            False   
4  False  False  False   False            False            False   

   Occurrence_Date  Occurrence_Year  Occurrence_Month  Occurrence_Day  ...  \
0            False            False             False           False  ...   
1            False            False             False           False  ...   
2            False            False             False           False  ...   
3            False            False             False           False  ...   
4            False            False             False           False  ...   

   Bike_Model  Bike_Type  Bike_Speed  Bike_Colour  Cost_of_Bike  Status  \
0        True      False       False        False          True   False   
1       False      False       False        False          True   False   
2        True      False       False        False         False   False   
3        True      False       False        False         False   False   
4        True      False       False        False         False   False   

   Hood_ID  Neighbourhood    Lat   Long  
0    False          False  False  False  
1    False          False  False  False  
2    False          False  False  False  
3    False          False  False  False  
4    False          False  False  False  

[5 rows x 26 columns]

In [181]:
for column in missing_data.columns.values.tolist():
    print(column)
    print (missing_data[column].value_counts())
    print("")   

X
False    21584
Name: X, dtype: int64

Y
False    21584
Name: Y, dtype: int64

FID
False    21584
Name: FID, dtype: int64

Index_
False    21584
Name: Index_, dtype: int64

event_unique_id
False    21584
Name: event_unique_id, dtype: int64

Primary_Offence
False    21584
Name: Primary_Offence, dtype: int64

Occurrence_Date
False    21584
Name: Occurrence_Date, dtype: int64

Occurrence_Year
False    21584
Name: Occurrence_Year, dtype: int64

Occurrence_Month
False    21584
Name: Occurrence_Month, dtype: int64

Occurrence_Day
False    21584
Name: Occurrence_Day, dtype: int64

Occurrence_Time
False    21584
Name: Occurrence_Time, dtype: int64

Division
False    21584
Name: Division, dtype: int64

City
False    21584
Name: City, dtype: int64

Location_Type
False    21584
Name: Location_Type, dtype: int64

Premise_Type
False    21584
Name: Premise_Type, dtype: int64

Bike_Make
False    21584
Name: Bike_Make, dtype: int64

Bike_Model
False    13443
True      8141
Name: Bike_Model, dtype: in

In [182]:
df_data_0.corr()

X         Y       FID    Index_  Occurrence_Year  \
X                 1.000000  0.256565 -0.016691 -0.016693        -0.019104   
Y                 0.256565  1.000000 -0.077388 -0.078740        -0.065970   
FID              -0.016691 -0.077388  1.000000  0.997760         0.981998   
Index_           -0.016693 -0.078740  0.997760  1.000000         0.982951   
Occurrence_Year  -0.019104 -0.065970  0.981998  0.982951         1.000000   
Occurrence_Month  0.006482 -0.001863  0.068585  0.072131         0.000731   
Occurrence_Day   -0.013571 -0.016574  0.019805  0.021676         0.017021   
Division          0.562853  0.097559 -0.016356 -0.016339        -0.022786   
Bike_Speed       -0.015446  0.011538  0.014114  0.015764        -0.007382   
Cost_of_Bike     -0.001311 -0.026285  0.017107  0.016984         0.032903   
Hood_ID           0.501374  0.038789 -0.007203 -0.006756        -0.009727   
Lat               0.256617  1.000000 -0.077409 -0.078762        -0.065990   
Long              1.000000  0.256565 -0.016691 -0.016693        -0.019104   

                  Occurrence_Month  Occurrence_Day  Division  Bike_Speed  \
X                         0.006482       -0.013571  0.562853   -0.015446   
Y                        -0.001863       -0.016574  0.097559    0.011538   
FID                       0.068585        0.019805 -0.016356    0.014114   
Index_                    0.072131        0.021676 -0.016339    0.015764   
Occurrence_Year           0.000731        0.017021 -0.022786   -0.007382   
Occurrence_Month          1.000000       -0.070054  0.018453    0.016599   
Occurrence_Day           -0.070054        1.000000 -0.009424    0.006709   
Division                  0.018453       -0.009424  1.000000    0.027743   
Bike_Speed                0.016599        0.006709  0.027743    1.000000   
Cost_of_Bike             -0.010444        0.006380  0.013912    0.025324   
Hood_ID                  -0.008436        0.002136  0.004252   -0.033813   
Lat                      -0.001864       -0.016571  0.097658    0.011530   
Long                      0.006482       -0.013571  0.562853   -0.015446   

                  Cost_of_Bike   Hood_ID       Lat      Long  
X                    -0.001311  0.501374  0.256617  1.000000  
Y                    -0.026285  0.038789  1.000000  0.256565  
FID                   0.017107 -0.007203 -0.077409 -0.016691  
Index_                0.016984 -0.006756 -0.078762 -0.016693  
Occurrence_Year       0.032903 -0.009727 -0.065990 -0.019104  
Occurrence_Month     -0.010444 -0.008436 -0.001864  0.006482  
Occurrence_Day        0.006380  0.002136 -0.016571 -0.013571  
Division              0.013912  0.004252  0.097658  0.562853  
Bike_Speed            0.025324 -0.033813  0.011530 -0.015446  
Cost_of_Bike          1.000000 -0.004965 -0.026273 -0.001311  
Hood_ID              -0.004965  1.000000  0.038889  0.501374  
Lat                  -0.026273  0.038889  1.000000  0.256617  
Long                 -0.001311  0.501374  0.256617  1.000000

In [235]:
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
address = 'TORONTO, TO'

geolocator = Nominatim(user_agent="to_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [236]:
toronto_data = df_data_0.loc[(df_data_0['Occurrence_Year']==2019)].reset_index(drop=True)
toronto_data.head()

X             Y    FID  Index_ event_unique_id  \
0 -8.840422e+06  5.413048e+06  17075   18130  GO-20191105157   
1 -8.835547e+06  5.414723e+06  17116   18131  GO-20191105288   
2 -8.836213e+06  5.414869e+06  17223   18132  GO-20191106490   
3 -8.841181e+06  5.417234e+06  17226   18133  GO-20191106615   
4 -8.841181e+06  5.417234e+06  17233   18134  GO-20191106615   

    Primary_Offence Occurrence_Date  Occurrence_Year  Occurrence_Month  \
0       THEFT UNDER      2019-06-14             2019                 6   
1  PROPERTY - FOUND      2019-06-14             2019                 6   
2  PROPERTY - FOUND      2019-06-15             2019                 6   
3      B&E W'INTENT      2019-06-08             2019                 6   
4      B&E W'INTENT      2019-06-08             2019                 6   

   Occurrence_Day  ...       Bike_Model  Bike_Type Bike_Speed Bike_Colour  \
0              14  ...  ZONE S                  EL          1      RED      
1              14  ...  TRANSFER 10             MT         21      BLKONG   
2              15  ...  XFR                     MT         24         NaN   
3               8  ...  OLTRAY                  RC         24      BLK      
4               8  ...  LEXA 3                  MT         18      BLK      

  Cost_of_Bike   Status Hood_ID                 Neighbourhood        Lat  \
0       2500.0   STOLEN      80  Palmerston-Little Italy (80)  43.660469   
1        500.0  UNKNOWN      74      North St.James Town (74)  43.671349   
2          NaN  UNKNOWN      98      Rosedale-Moore Park (98)  43.672302   
3      10000.0   STOLEN     106      Humewood-Cedarvale (106)  43.687664   
4       1500.0   STOLEN     106      Humewood-Cedarvale (106)  43.687664   

        Long  
0 -79.414864  
1 -79.371071  
2 -79.377052  
3 -79.421684  
4 -79.421684  

[5 rows x 26 columns]

In [185]:
toronto_data.shape

(3673, 26)

In [237]:
# create map of Toronto using latitude and longitude values
map_toronto2 = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, neighborhood in zip(toronto_data['Lat'], toronto_data['Long'], toronto_data['Neighbourhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto2)  
    
map_toronto2

In [238]:
neighborhood_latitude = toronto_data.loc[0, 'Lat'] # neighborhood latitude value
neighborhood_longitude = toronto_data.loc[0, 'Long'] # neighborhood longitude value

neighborhood_name = toronto_data.loc[0, 'Neighbourhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Palmerston-Little Italy (80) are 43.6604691, -79.4148636.


In [239]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=JRBHXSAPVLFOMM3HB1JTGFOR4KPPWXALLREDW4ZY0RBFNB25&client_secret=GJSLRP4TE2DLT300PQLVZTQXBH41PFYGMRORADYWUEEJEO5P&v=20180605&ll=43.6604691,-79.4148636&radius=500&limit=100'

In [248]:
toronto_grouped = toronto_data.groupby('Neighbourhood').mean().reset_index()
toronto_grouped

Neighbourhood             X             Y  \
0        Agincourt South-Malvern West (128) -8.823312e+06  5.432883e+06   
1                            Alderwood (20) -8.855529e+06  5.404826e+06   
2                                Annex (95) -8.839044e+06  5.414714e+06   
3                    Banbury-Don Mills (42) -8.831312e+06  5.423893e+06   
4                       Bathurst Manor (34) -8.845288e+06  5.427678e+06   
5                  Bay Street Corridor (76) -8.836945e+06  5.412523e+06   
6                      Bayview Village (52) -8.836195e+06  5.430021e+06   
7                Bayview Woods-Steeles (49) -8.837028e+06  5.433782e+06   
8                 Bedford Park-Nortown (39) -8.841321e+06  5.423520e+06   
9             Beechborough-Greenbrook (112) -8.847381e+06  5.417534e+06   
10                            Bendale (127) -8.822908e+06  5.429389e+06   
11              Birchcliffe-Cliffside (122) -8.823372e+06  5.419429e+06   
12                         Black Creek (24) -8.851375e+06  5.428971e+06   
13                         Blake-Jones (69) -8.832069e+06  5.415571e+06   
14               Briar Hill-Belgravia (108) -8.844562e+06  5.418991e+06   
15   Bridle Path-Sunnybrook-York Mills (41) -8.837338e+06  5.423398e+06   
16                     Broadview North (57) -8.833564e+06  5.416919e+06   
17                 Brookhaven-Amesbury (30) -8.849093e+06  5.419284e+06   
18     Cabbagetown-South St.James Town (71) -8.835465e+06  5.413870e+06   
19                           Casa Loma (96) -8.839688e+06  5.416074e+06   
20             Centennial Scarborough (133) -8.810205e+06  5.432318e+06   
21               Church-Yonge Corridor (75) -8.836498e+06  5.412953e+06   
22                Clairlea-Birchmount (120) -8.825504e+06  5.421700e+06   
23                        Clanton Park (33) -8.843005e+06  5.425671e+06   
24                         Cliffcrest (123) -8.820989e+06  5.421294e+06   
25              Corso Italia-Davenport (92) -8.843544e+06  5.415767e+06   
26                            Danforth (66) -8.831124e+06  5.416536e+06   
27                  Danforth East York (59) -8.830742e+06  5.417348e+06   
28                  Don Valley Village (47) -8.833074e+06  5.431719e+06   
29                        Dorset Park (126) -8.825665e+06  5.425395e+06   
..                                      ...           ...           ...   
103               Scarborough Village (139) -8.818864e+06  5.425942e+06   
104                     South Parkdale (85) -8.842103e+06  5.409652e+06   
105                    South Riverdale (70) -8.832168e+06  5.413382e+06   
106               St.Andrew-Windfields (40) -8.836464e+06  5.426758e+06   
107                Stonegate-Queensway (16) -8.849863e+06  5.409137e+06   
108            Tam O'Shanter-Sullivan (118) -8.828293e+06  5.431205e+06   
109                      Taylor-Massey (61) -8.827084e+06  5.418135e+06   
110                        The Beaches (63) -8.827720e+06  5.414758e+06   
111                   Thorncliffe Park (55) -8.833658e+06  5.420205e+06   
112                  Trinity-Bellwoods (81) -8.840417e+06  5.411535e+06   
113                         University (79) -8.838906e+06  5.413427e+06   
114                   Victoria Village (43) -8.828156e+06  5.422037e+06   
115  Waterfront Communities-The Island (77) -8.837276e+06  5.410494e+06   
116                         West Hill (136) -8.815093e+06  5.429188e+06   
117              West Humber-Clairville (1) -8.860682e+06  5.423693e+06   
118                Westminster-Branson (35) -8.844070e+06  5.432092e+06   
119                            Weston (113) -8.851475e+06  5.419389e+06   
120                 Weston-Pellam Park (91) -8.845099e+06  5.414906e+06   
121                  Wexford/Maryvale (119) -8.827465e+06  5.426644e+06   
122                    Willowdale East (51) -8.839582e+06  5.429436e+06   
123                    Willowdale West (37) -8.841014e+06  5.430307e+06   
124    Willowridge-Martingrove-Richview (7) -8.856948e+

In [249]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighbourhood'] = toronto_grouped['Neighbourhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighbourhood 1st Most Common Venue  \
0  Agincourt South-Malvern West (128)                     Y   
1                      Alderwood (20)                     Y   
2                          Annex (95)                     Y   
3              Banbury-Don Mills (42)                     Y   
4                 Bathurst Manor (34)                     Y   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                   FID                Index_       Occurrence_Year   
1                Index_                   FID       Occurrence_Year   
2                Index_                   FID       Occurrence_Year   
3                Index_                   FID       Occurrence_Year   
4                Index_                   FID       Occurrence_Year   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0          Cost_of_Bike               Hood_ID                   Lat   
1          Cost_of_Bike                   Lat              Division   
2          Cost_of_Bike               Hood_ID                   Lat   
3          Cost_of_Bike                   Lat               Hood_ID   
4          Cost_of_Bike                   Lat               Hood_ID   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0              Division        Occurrence_Day       Occurrence_Month  
1               Hood_ID        Occurrence_Day             Bike_Speed  
2              Division        Occurrence_Day             Bike_Speed  
3              Division            Bike_Speed       Occurrence_Month  
4              Division            Bike_Speed         Occurrence_Day

In [251]:
# import k-means from clustering stage
from sklearn.cluster import KMeans

# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([3, 0, 2, 1, 1, 2, 1, 1, 1, 0], dtype=int32)

In [254]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = toronto_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')

toronto_merged.head() # check the last columns!

ValueError: cannot insert Cluster Labels, already exists

In [256]:
toronto_merged.head()

X             Y    FID  Index_ event_unique_id  \
0 -8.840422e+06  5.413048e+06  17075   18130  GO-20191105157   
1 -8.835547e+06  5.414723e+06  17116   18131  GO-20191105288   
2 -8.836213e+06  5.414869e+06  17223   18132  GO-20191106490   
3 -8.841181e+06  5.417234e+06  17226   18133  GO-20191106615   
4 -8.841181e+06  5.417234e+06  17233   18134  GO-20191106615   

    Primary_Offence Occurrence_Date  Occurrence_Year  Occurrence_Month  \
0       THEFT UNDER      2019-06-14             2019                 6   
1  PROPERTY - FOUND      2019-06-14             2019                 6   
2  PROPERTY - FOUND      2019-06-15             2019                 6   
3      B&E W'INTENT      2019-06-08             2019                 6   
4      B&E W'INTENT      2019-06-08             2019                 6   

   Occurrence_Day  ...       Bike_Model  Bike_Type Bike_Speed Bike_Colour  \
0              14  ...  ZONE S                  EL          1      RED      
1              14  ...  TRANSFER 10             MT         21      BLKONG   
2              15  ...  XFR                     MT         24         NaN   
3               8  ...  OLTRAY                  RC         24      BLK      
4               8  ...  LEXA 3                  MT         18      BLK      

  Cost_of_Bike   Status Hood_ID                 Neighbourhood        Lat  \
0       2500.0   STOLEN      80  Palmerston-Little Italy (80)  43.660469   
1        500.0  UNKNOWN      74      North St.James Town (74)  43.671349   
2          NaN  UNKNOWN      98      Rosedale-Moore Park (98)  43.672302   
3      10000.0   STOLEN     106      Humewood-Cedarvale (106)  43.687664   
4       1500.0   STOLEN     106      Humewood-Cedarvale (106)  43.687664   

        Long  
0 -79.414864  
1 -79.371071  
2 -79.377052  
3 -79.421684  
4 -79.421684  

[5 rows x 26 columns]

In [257]:
toronto_merged.shape

(3673, 26)

In [255]:
# create map
import matplotlib.cm as cm
import matplotlib.colors as colors

map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Lat'], toronto_merged['Long'], toronto_merged['Neighbourhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

KeyError: 'Cluster Labels'

KeyError: 'Cluster Labels'